# Importing the data

In [11]:
import pandas as pd

# Load the newly uploaded dataset to analyze its structure and identify key columns for stemming
file_path = 'Data.csv'
data = pd.read_csv(file_path)

df = pd.DataFrame(data)

# Display the first few rows and summary information to identify key columns for stemming
data.head(), data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500 entries, 0 to 499
Data columns (total 12 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   Job Title                489 non-null    object 
 1   Applicant ID             500 non-null    int64  
 2   Job Experience Required  500 non-null    object 
 3   Key Skills               500 non-null    object 
 4   Role Category            463 non-null    object 
 5   Location                 489 non-null    object 
 6   Functional Area          489 non-null    object 
 7   Industry                 489 non-null    object 
 8   Role                     486 non-null    object 
 9   Longitude                473 non-null    float64
 10  Latitude                 473 non-null    float64
 11  sal                      500 non-null    int64  
dtypes: float64(2), int64(2), object(8)
memory usage: 47.0+ KB


(                                                    Job Title  Applicant ID Job Experience Required                                                                                           Key Skills                               Role Category   Location                                      Functional Area                               Industry                              Role  Longitude   Latitude   sal
 0                                       Digital Media Planner             1              5 - 10 yrs                                                                        Media Planning| Digital Media                                 Advertising     Mumbai   Marketing , Advertising , MR , PR , Media Planning  Advertising, PR, MR, Event Management  Media Planning Executive/Manager  72.877393  19.075990  3855
 1                                    Online Bidding Executive             2               2 - 5 yrs   pre sales| closing| software knowledge| clients| requirements| negotiating|

# Stemming the Data

In [12]:
import nltk
nltk.download('punkt_tab')
from nltk.stem import PorterStemmer
from nltk.tokenize import word_tokenize
import pandas as pd

# Download required NLTK resources

# Initialize the Porter Stemmer
stemmer = PorterStemmer()

# Function to apply stemming
def stem_text(text):
    if pd.isnull(text):  # Handle missing values
        return ""
    words = word_tokenize(text)  # Tokenize the text
    stemmed_words = [stemmer.stem(word) for word in words]  # Apply stemming
    return " ".join(stemmed_words)  # Rejoin words into a string

# Apply stemming to the relevant columns
for column in ['Job Title', 'Key Skills', 'Functional Area','Role Category' ]:
    df[f'{column} Stemmed'] = df[column].apply(stem_text)

# df = pd.DataFrame(data)
# Display the updated DataFrame
df[['Job Title', 'Job Title Stemmed', 'Key Skills', 'Key Skills Stemmed', 'Functional Area', 'Functional Area Stemmed','Role Category','Role Category Stemmed']].head()


[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\Acer\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


Job Title                                   Job Title Stemmed                                                                                           Key Skills                                                                                   Key Skills Stemmed                                      Functional Area                   Functional Area Stemmed                               Role Category                 Role Category Stemmed
0                                       Digital Media Planner                                 digit media planner                                                                        Media Planning| Digital Media                                                                          media planning| digit media   Marketing , Advertising , MR , PR , Media Planning  market , advertis , mr , pr , media plan                                 Advertising                              advertis
1                                    Online Bidding Executive                                    onlin bid execut   pre sales| closing| software knowledge| clients| requirements| negotiating| client| online bidd...  pre sales| closing| softwar knowledge| clients| requirements| negotiating| client| onlin bidding...                Sales , Retail , Business Development              sale , retail , busi develop                                Retail Sales                           retail sale
2   Trainee Research/ Research Executive- Hi- Tech Operations  traine research/ research executive- hi- tech oper   Computer science| Fabrication| Quality check| Intellectual property| Electronics| Support servi...  comput science| fabrication| qualiti check| intellectu property| electronics| support services| ...                             Engineering Design , R&D                      engin design , r & d                                         R&D                                 r & d
3                                           Technical Support                                     technic support                                                                                    Technical Support                                                                                      technic support  IT Software - Application Programming , Maintenance     it softwar - applic program , mainten  Admin/Maintenance/Security/Datawarehousing  admin/maintenance/security/datawareh
4                           Software Test Engineer -hyderabad                       softwar test engin -hyderabad                          manual testing| test engineering| test cases| web testing| web technologies                             manual testing| test engineering| test cases| web testing| web technolog                           IT Software - QA & Testing                    it softwar - qa & test                        Programming & Design                      program & design

# Normalising the Salary and Adjusting maximum and minimum Experience


In [13]:
from sklearn.preprocessing import MinMaxScaler

scaler = MinMaxScaler()
df['sal_normalized'] = scaler.fit_transform(data[['sal']])

df[['min_experience', 'max_experience']] = data['Job Experience Required'].str.extract(r'(\d+)\s*-\s*(\d+)').astype(float)


# Taking the preprocessed Column and droping the orignal columns

In [14]:
# Replace the original column with the preprocessed one
df['Job Title'] = df['Job Title Stemmed']
df['Functional Area'] = df['Functional Area Stemmed']
df['Key Skills'] = df['Key Skills Stemmed']
df['Role Category'] = df['Role Category Stemmed']

# Drop temporary columns (if needed)
df.drop(['Job Title Stemmed', 'Functional Area Stemmed','Key Skills Stemmed','Role Category Stemmed'], axis=1, inplace=True)

# 'Key Skills', 'Key Skills Stemmed', 'Functional Area', 'Functional Area Stemmed','Role Category','Role Category Stemmed

In [15]:
df_cleaned = df.dropna(subset=['Job Title', 'Role Category', 'Functional Area', 'Key Skills'], how='all')
df_cleaned1 = df_cleaned.dropna(subset=['Role'])
df_cleaned1.info()

<class 'pandas.core.frame.DataFrame'>
Index: 486 entries, 0 to 499
Data columns (total 15 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   Job Title                486 non-null    object 
 1   Applicant ID             486 non-null    int64  
 2   Job Experience Required  486 non-null    object 
 3   Key Skills               486 non-null    object 
 4   Role Category            486 non-null    object 
 5   Location                 486 non-null    object 
 6   Functional Area          486 non-null    object 
 7   Industry                 486 non-null    object 
 8   Role                     486 non-null    object 
 9   Longitude                459 non-null    float64
 10  Latitude                 459 non-null    float64
 11  sal                      486 non-null    int64  
 12  sal_normalized           486 non-null    float64
 13  min_experience           486 non-null    float64
 14  max_experience           486 no

# IDF Vectorization

In [16]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Example dataframe (replace with your actual dataframe)
# Ensure the relevant columns are clean and contain textual data
columns_to_vectorize = ['Job Title', 'Functional Area', 'Key Skills', 'Role Category']

# Initialize TfidfVectorizer
vectorizers = {col: TfidfVectorizer() for col in columns_to_vectorize}

# Transform each column
idf_vectors = {}
for col in columns_to_vectorize:
    idf_vectors[col] = vectorizers[col].fit_transform(df_cleaned1[col].fillna(""))

# If you want to concatenate all the vectors into one matrix
from scipy.sparse import hstack
combined_idf_vector = hstack([idf_vectors[col] for col in columns_to_vectorize])

# Example: Access individual column IDF vectors
print(idf_vectors['Job Title'])  # Sparse matrix for 'Job Title'
print(combined_idf_vector)       # Combined sparse matrix


<Compressed Sparse Row sparse matrix of dtype 'float64'
	with 2154 stored elements and shape (486, 766)>
  Coords	Values
  (0, 225)	0.4882606347969171
  (0, 450)	0.5686245281240289
  (0, 538)	0.6620178989449131
  (1, 503)	0.6640815875922913
  (1, 111)	0.6640815875922913
  (1, 267)	0.3434986026780953
  (2, 710)	0.3531897998693059
  (2, 597)	0.7063795997386118
  (2, 268)	0.30404791624820043
  (2, 332)	0.376706109878592
  (2, 683)	0.25984504557937055
  (2, 509)	0.27278700488571406
  (3, 685)	0.7027945616208835
  (3, 671)	0.7113928620362381
  (4, 648)	0.4926085438407425
  (4, 693)	0.6020289215230081
  (4, 259)	0.358993916073228
  (4, 349)	0.5157725936954726
  (5, 507)	0.3486268772732622
  (5, 287)	0.24694954277877396
  (5, 29)	0.5587221552350018
  (5, 44)	0.5587221552350018
  (5, 652)	0.43947051125548536
  (6, 287)	0.2329984027023458
  (6, 609)	0.4942493408450334
  :	:
  (481, 685)	0.266169750936162
  (481, 187)	0.2935187098944045
  (481, 247)	0.36834755272148834
  (481, 94)	0.316864319815

# Logistic Regression

In [17]:
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
import seaborn as sns
import matplotlib.pyplot as plt


# Split the data into features (X) and target (y)
X = combined_idf_vector  # Features
y = df_cleaned1['Role']  # Target column (Role)

# Split the data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Train the Logistic Regression model
model = LogisticRegression(max_iter=500)
model.fit(X_train, y_train)

# Predict the target variable on the test set
y_pred = model.predict(X_test)

# Print the classification report
print("Without PCA and Feature Engineering - Classification Report:")
report_dict = classification_report(y_test, y_pred, output_dict=True)

# Convert it to a pandas DataFrame
report_df = pd.DataFrame(report_dict).transpose()

pd.set_option('display.max_colwidth', 100)
pd.set_option('display.expand_frame_repr', False)

print(report_df)

# Print the accuracy score
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy: {accuracy:.4f}")

# Confusion Matrix
conf_matrix = confusion_matrix(y_test, y_pred)
print("Confusion Matrix:")
print(conf_matrix)

# Plotting the Confusion Matrix
plt.figure(figsize=(10, 7))
sns.heatmap(conf_matrix, annot=True, fmt="d", cmap="Blues", xticklabels=model.classes_, yticklabels=model.classes_)
plt.xlabel("Predicted")
plt.ylabel("True")
plt.title("Confusion Matrix")
plt.show()




Without PCA and Feature Engineering - Classification Report:
                                                                                                      precision    recall  f1-score    support
Accounts Executive/Accountant                                                                          0.714286  1.000000  0.833333   5.000000
Accounts Manager                                                                                       0.000000  0.000000  0.000000   1.000000
Architect                                                                                              0.500000  0.333333  0.400000   3.000000
Area Sales Manager                                                                                     0.000000  0.000000  0.000000   1.000000
Associate/Senior Associate -(NonTechnical)                                                             0.666667  1.000000  0.800000   6.000000
Associate/Senior Associate -(Technical)                                          

c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{

In [18]:
from sklearn.decomposition import PCA

# Target column
y = df_cleaned1['Role']  # Assuming 'Role' is the target column
X = combined_idf_vector

# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Apply PCA to reduce dimensionality
pca = PCA(n_components=0.85)  
X_train_pca = pca.fit_transform(X_train.toarray())
X_test_pca = pca.transform(X_test.toarray())

# Logistic Regression Model
model = LogisticRegression(max_iter=500)
model.fit(X_train_pca, y_train)

# Make predictions
y_pred = model.predict(X_test_pca)

# Evaluate the model
print("Classification Report:")
report_dict = classification_report(y_test, y_pred, output_dict=True)

# Convert it to a pandas DataFrame
report_df = pd.DataFrame(report_dict).transpose()

# Display it with text wrapping
pd.set_option('display.max_colwidth', 100)
pd.set_option('display.expand_frame_repr', False)

print(report_df)

print("Accuracy Score:", accuracy_score(y_test, y_pred))

print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))


Classification Report:
                                                                                                      precision    recall  f1-score    support
Accounts Executive/Accountant                                                                          0.714286  1.000000  0.833333   5.000000
Accounts Manager                                                                                       0.000000  0.000000  0.000000   1.000000
Architect                                                                                              0.500000  0.333333  0.400000   3.000000
Area Sales Manager                                                                                     0.000000  0.000000  0.000000   1.000000
Associate/Senior Associate -(NonTechnical)                                                             0.666667  1.000000  0.800000   6.000000
Associate/Senior Associate -(Technical)                                                                0.000000  0.0000

c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{

# GMM


In [23]:
from collections import Counter

# Map clusters to roles using majority voting, with safeguards for empty clusters
cluster_to_role = {}
for cluster in range(n_roles):
    indices = np.where(gmm_clusters == cluster)
    true_labels = y_test.iloc[indices]
    
    if len(true_labels) > 0:
        # Use Counter to find the most common true label
        most_common_role = Counter(true_labels).most_common(1)[0][0]
        cluster_to_role[cluster] = most_common_role
    else:
        # Handle empty cluster by assigning a placeholder or skipping
        cluster_to_role[cluster] = None

# Map clusters to actual roles, handling unmapped clusters
gmm_pred_roles = [cluster_to_role[cluster] if cluster_to_role[cluster] is not None else "Unknown" for cluster in gmm_clusters]

# Step 4: Evaluate the performance
print("Classification Report for GMM:")
# print(classification_report(y_test, gmm_pred_roles))

report_dict = classification_report(y_test, gmm_pred_roles, output_dict=True)

# Convert it to a pandas DataFrame
report_df = pd.DataFrame(report_dict).transpose()

# Display it with text wrapping
pd.set_option('display.max_colwidth', 100)
pd.set_option('display.expand_frame_repr', False)

print(report_df)

# Optional: Compute Adjusted Rand Index (ARI) for clustering
ari = adjusted_rand_score(y_test, gmm_pred_roles)
print(f"Adjusted Rand Index (ARI): {ari:.4f}")

from sklearn.metrics import accuracy_score

# Calculate accuracy
accuracy = accuracy_score(y_test, gmm_pred_roles)

print(f"GMM Classification Accuracy: {accuracy:.4f}")

Classification Report for GMM:
                                                                                                      precision    recall  f1-score    support
Accounts Executive/Accountant                                                                          0.833333  1.000000  0.909091   5.000000
Accounts Manager                                                                                       0.000000  0.000000  0.000000   1.000000
Architect                                                                                              0.750000  1.000000  0.857143   3.000000
Area Sales Manager                                                                                     0.000000  0.000000  0.000000   1.000000
Associate/Senior Associate -(NonTechnical)                                                             0.750000  1.000000  0.857143   6.000000
Associate/Senior Associate -(Technical)                                                                0.000000

c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\Acer\AppData\Local\Programs\Python\Python312\Lib\site-packages\sklearn\metrics\_classification.py:1531: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modif